How do we quantify each station, define the worth of it to justify allocating resources? There must be a formula.  Also, we must use the industry standards.  We want to use a map in some capacity!

In [2]:
import pandas as pd
import numpy as np
import matplotlib as plt
from datetime import date
from datetime import time
from datetime import datetime

from IPython.display import Image

# various options in pandas
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 25)
pd.set_option('display.precision', 3)

df = pd.read_csv('turnstile_171007.csv')
series= df['C/A'].str.strip()
fin  = {}

df.columns = df.columns.str.strip()
new_val = []
value = []
print(df.head())

    C/A  UNIT       SCP STATION LINENAME DIVISION        DATE      TIME  \
0  A002  R051  02-00-00   59 ST  NQR456W      BMT  09/30/2017  00:00:00   
1  A002  R051  02-00-00   59 ST  NQR456W      BMT  09/30/2017  04:00:00   
2  A002  R051  02-00-00   59 ST  NQR456W      BMT  09/30/2017  08:00:00   
3  A002  R051  02-00-00   59 ST  NQR456W      BMT  09/30/2017  12:00:00   
4  A002  R051  02-00-00   59 ST  NQR456W      BMT  09/30/2017  16:00:00   

      DESC  ENTRIES    EXITS  
0  REGULAR  6346858  2147624  
1  REGULAR  6346893  2147630  
2  REGULAR  6346912  2147655  
3  REGULAR  6347003  2147741  
4  REGULAR  6347270  2147801  


In [25]:
mta_dict = {}
for i in range(len(df.index)):
    # Create the desired key and value
    key_i = (df['C/A'][i], df.UNIT[i], df.SCP[i], df.STATION[i]) # make easier by calling [0:4]
    value_i = [df.LINENAME[i], df.DIVISION[i], df.DATE[i], df.TIME[i], df.DESC[i], df.ENTRIES[i], df.EXITS[i]]
    
    if key_i in mta_dict:
        current = mta_dict[key_i]
        current.append(value_i)
        mta_dict[key_i] = current
    
    else:
        mta_dict[key_i] = [value_i]
mta_dict

{('A002',
  'R051',
  '02-00-00',
  '59 ST'): [['NQR456W',
   'BMT',
   '09/30/2017',
   '00:00:00',
   'REGULAR',
   6346858,
   2147624], ['NQR456W',
   'BMT',
   '09/30/2017',
   '04:00:00',
   'REGULAR',
   6346893,
   2147630], ['NQR456W',
   'BMT',
   '09/30/2017',
   '08:00:00',
   'REGULAR',
   6346912,
   2147655], ['NQR456W',
   'BMT',
   '09/30/2017',
   '12:00:00',
   'REGULAR',
   6347003,
   2147741], ['NQR456W',
   'BMT',
   '09/30/2017',
   '16:00:00',
   'REGULAR',
   6347270,
   2147801], ['NQR456W',
   'BMT',
   '09/30/2017',
   '20:00:00',
   'REGULAR',
   6347620,
   2147838], ['NQR456W',
   'BMT',
   '10/01/2017',
   '00:00:00',
   'REGULAR',
   6347820,
   2147853], ['NQR456W',
   'BMT',
   '10/01/2017',
   '04:00:00',
   'REGULAR',
   6347837,
   2147862], ['NQR456W',
   'BMT',
   '10/01/2017',
   '08:00:00',
   'REGULAR',
   6347847,
   2147880], ['NQR456W',
   'BMT',
   '10/01/2017',
   '12:00:00',
   'REGULAR',
   6347940,
   2147937], ['NQR456W',
   'BMT',
 

# Challenge 2

Let's turn this into a time series.

For each key (basically the control area, unit, device address and station of a specific turnstile), have a list again, but let the list be comprised of just the point in time and the count of entries.

This basically means keeping only the date, time, and entries fields in each list. You can convert the date and time into datetime objects -- That is a python class that represents a point in time. You can combine the date and time fields into a string and use the dateutil module to convert it into a datetime object. For an example check this StackOverflow question.

Your new dict should look something like

{ ('A002','R051','02-00-00','LEXINGTON AVE'): [ [datetime.datetime(2013, 3, 2, 3, 0), 3788], [datetime.datetime(2013, 3, 2, 7, 0), 2585], [datetime.datetime(2013, 3, 2, 12, 0), 10653], [datetime.datetime(2013, 3, 2, 17, 0), 11016], [datetime.datetime(2013, 3, 2, 23, 0), 10666], [datetime.datetime(2013, 3, 3, 3, 0), 10814], [datetime.datetime(2013, 3, 3, 7, 0), 10229], ... ], .... }

In [89]:
#importing and initializing new packages and variables
import dateutil.parser
from datetime import *
time_dict = {}
datetime = ''


#look closer at the data, where is the first ENTRIES point
#similar for loop as above but with some variables removed, and satetime added
for i in range(len(df.index)):
    if i !=0:
        # Create the desired key and value
        key = (df['C/A'][i], df.UNIT[i], df.SCP[i], df.STATION[i]) # make easier by calling [0:4]
        datetime = df.DATE[i]+ ' ' + df.TIME[i]
        
        value = [dateutil.parser.parse(datetime), df.ENTRIES[i] - df.ENTRIES[(i-1)]]
        if (df.ENTRIES[i] - df.ENTRIES[(i-1)])>0:
            if key in time_dict:
                current = time_dict[key]
                current.append(value)
                time_dict[key] = current
    
            else:
                time_dict[key] = [value]
        
time_dict

{('A002',
  'R051',
  '02-00-00',
  '59 ST'): [[datetime.datetime(2017, 9, 30, 4, 0),
   35], [datetime.datetime(2017, 9, 30, 8, 0), 19], [datetime.datetime(2017, 9, 30, 12, 0),
   91], [datetime.datetime(2017, 9, 30, 16, 0),
   267], [datetime.datetime(2017, 9, 30, 20, 0), 350], [datetime.datetime(2017, 10, 1, 0, 0),
   200], [datetime.datetime(2017, 10, 1, 4, 0),
   17], [datetime.datetime(2017, 10, 1, 8, 0), 10], [datetime.datetime(2017, 10, 1, 12, 0),
   93], [datetime.datetime(2017, 10, 1, 16, 0),
   207], [datetime.datetime(2017, 10, 1, 20, 0), 334], [datetime.datetime(2017, 10, 2, 0, 0),
   120], [datetime.datetime(2017, 10, 2, 4, 0),
   13], [datetime.datetime(2017, 10, 2, 8, 0), 50], [datetime.datetime(2017, 10, 2, 12, 0),
   162], [datetime.datetime(2017, 10, 2, 16, 0),
   381], [datetime.datetime(2017, 10, 2, 20, 0), 920], [datetime.datetime(2017, 10, 3, 0, 0),
   215], [datetime.datetime(2017, 10, 3, 4, 0),
   16], [datetime.datetime(2017, 10, 3, 8, 0), 33], [datetime.datet

#### Challenge 3

- These counts are for every n hours. (What is n?) We want total daily
  entries.

Now make it that we again have the same keys, but now we have a single
value for a single day, which is the total number of passengers that
entered through this turnstile on this day.


In [103]:
#Getting Unique dates in DF
new_col = []
for i in range(len(df.DATE)):
    date = dateutil.parser.parse(df['DATE'][i])
    new_col.append(date)
df['datetime'] = new_col
fin_df = df.groupby(['C/A', 'UNIT', 'SCP', 'STATION', 'datetime'])['ENTRIES'].max()
min_df = df.groupby(['C/A', 'UNIT', 'SCP', 'STATION', 'datetime'])['ENTRIES'].min()

#Replaces max value with Cumulative
count=0
for i,z in zip(fin_df,min_df):
    fin_df[count] = i-z
    count +=1


C/A    UNIT  SCP       STATION        datetime  
A002   R051  02-00-00  59 ST          2017-09-30    6347620
                                      2017-10-01    6348481
                                      2017-10-02    6350127
                                      2017-10-03    6351673
                                      2017-10-04    6353253
                                      2017-10-05    6354816
                                      2017-10-06    6356292
             02-00-01  59 ST          2017-09-30    5721126
                                      2017-10-01    5721428
                                      2017-10-02    5722239
                                      2017-10-03    5723362
                                      2017-10-04    5724478
                                                     ...   
TRAM2  R469  00-00-00  RIT-ROOSEVELT  2017-10-02    3896650
                                      2017-10-03    3897820
                                      2017-10-04   

In [ ]:
cumulative =[]
for i in fin_df.index:
    cumulative.append(fin_df[i])
print(cumulative)

#### Challenge 4

We will plot the daily time series for a turnstile.

In ipython notebook, add this to the beginning of your next cell:
```Python
    %matplotlib inline
```
This will make your matplotlib graphs integrate nicely with the
notebook. To plot the time series, import matplotlib with
```Python
    import matplotlib.pyplot as plt
```
Take the list of [(date1, count1), (date2, count2), ...], for the
turnstile and turn it into two lists:
dates and counts. This should plot it:
```Python
    plt.figure(figsize=(10,3))
    plt.plot(dates,counts)
```

In [70]:
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

dates = dent.keys()
count = dent.values()
plt.figure(figsize=(10,3))
plt.plot(dates,counts)

NameError: name 'counts' is not defined

#### Challenge 5

- So far we've been operating on a single turnstile level, let's
  combine turnstiles in the same ControlArea/Unit/Station combo. There
  are some ControlArea/Unit/Station groups that have a single
  turnstile, but most have multiple turnstilea-- same value for the
  C/A, UNIT and STATION columns, different values for the SCP column.

We want to combine the numbers together -- for each
ControlArea/UNIT/STATION combo, for each day, add the counts from each
turnstile belonging to that combo.

#### Challenge 6

Similarly, combine everything in each station, and come up with a time
series of `[(date1, count1),(date2,count2),...]` type of time series
for each STATION, by adding up all the turnstiles in a station.

#### Challenge 7

Plot the time series for a station.

#### Challenge 8

- Make one list of counts for **one** week for one station. Monday's
count, Tuesday's count, etc. so it's a list of 7 counts.
Make the same list for another week, and another week, and another
week.
`plt.plot(week_count_list)` for every `week_count_list` you created
this way. You should get a rainbow plot of weekly commute numbers on
top of each other.

#### Challenge 9

- Over multiple weeks, sum total ridership for each station and sort
  them, so you can find out the stations with the highest traffic
  during the time you investigate

#### Challenge 10

- Make a single list of these total ridership values and plot it with

    plt.hist(total_ridership_counts)

to get an idea about the distribution of total ridership among
different stations.

This should show you that most stations have a small traffic, and the
histogram bins for large traffic volumes have small bars.

*Additional Hint*:

If you want to see which stations take the meat of the traffic, you
can sort the total ridership counts and make a `plt.bar` graph. For
this, you want to have two lists: the indices of each bar, and the
values. The indices can just be `0,1,2,3,...`, so you can do

    indices = range(len(total_ridership_values))
    plt.bar(indices, total_ridership_values)
